# Cyclotomic Generating Functions Notebook #

Written by *Sara Billey and Joshua P. Swanson*. Revision as of *May 3rd, 2023*.

**Overview**: This notebook is a companion to our paper, "Cyclotomic Generating Functions." It includes routines for testing if a polynomial is a CGF, for converting CGF's to cyclotomic or rational forms, and for iterating over the elements and minimal generating sets of the cyclotomic monoids $\Phi^{\pm}$, $\Phi^{+}$, $\Phi^{\mathrm{Gale}}$, $\Phi^{\mathrm{uni}}$, $\Phi^{\mathrm{lcc}}$. In particular, this code may be used to regenerate the tables in the Appendix and the associated OEIS entries:

| $\mathcal{M}$          | $|\mathcal{M}_n|$ | Irreducibles |
|------------------------|-------------------|--------------|
| $\Phi^{\mathrm{lcc}}$  | [A360622](https://oeis.org/A360622) | [A361439](https://oeis.org/A361439) |
| $\Phi^{\mathrm{uni}}$  | [A360621](https://oeis.org/A360621) | [A361440](https://oeis.org/A361440) |
| $\Phi^{\mathrm{Gale}}$ | [A362553](https://oeis.org/A362553) | [A362554](https://oeis.org/A362554) |
| $\Phi^{+}$             | [A360620](https://oeis.org/A360620) | [A361441](https://oeis.org/A361441) |
| $\Phi^{\pm}$           | [A120963](https://oeis.org/A120963) | [A014197](https://oeis.org/A014197) |

This notebook should be run on a SageMath kernel. It has been tested on SageMath 9.8.

## Initialization code ##

Run the following cell at startup.

In [1]:
import itertools
from collections import Counter

#------------------------------------------------------
#-------- General routines and helper functions -------
#------------------------------------------------------

R.<q> = QQ[]

@cached_function
def euler_phi_inverse(k):
    '''Returns a list of all n such that euler_phi(n) = k.
    
       INPUT:
       
       - ``k`` - an integer
       
       EXAMPLES::
       
           sage: euler_phi_inverse(8)
           [15, 16, 20, 24, 30]

           sage: euler_phi_inverse(9)
           []
    '''
    # We have elementary bounds sqrt(n)/2 <= euler_phi(n) <= n.
    # While this is very naive, it is not the bottleneck for our use case.
    return [n for n in range(k, 2*k^2+1) if euler_phi(n)==k]

def flatten(L):
    '''Flattens a list of lists into a single list.'''
    return [item for sublist in L for item in sublist]

def comps(L, n):
    '''Iterates over all lists of length n using some number (possibly zero)
       of L[0]'s followed by some number of L[1]'s, etc.'''
    for alpha in Compositions(n+len(L), length=len(L)):
        ret = []
        for i in range(len(L)):
            for _ in range(alpha[i]-1):
                ret.append(L[i])
        yield ret

#------------------------------------------------------
#--------- CGF testing and conversion routines --------
#------------------------------------------------------

@cached_method
def cached_cyclotomic_polynomial(n):
    return cyclotomic_polynomial(n, var=q)

def _cyclotomic_form_to_polynomial(L):
    # Returns the product of Phi_m for m in L
    return product(map(cached_cyclotomic_polynomial, L))

def CGF_to_cyclotomic_form(f, indexes_only=False):
    '''Takes a polynomial `f(q)`. Returns a factorization of `f` consisting of a
       constant times cyclotomic polynomials and `q`'s. Raises an error if
       `f` cannot be so factored.
       
       Note: the powers of ``q`` are collected onto the unit portion of the
       factorization.
       
       INPUT:
       
       - ``f`` - a polynomial in one variable `q`
       - ``indexes_only`` - boolean (default: ``False``). If ``True``, replaces the
         cyclotomic polynomial ``Phi_n`` with simply ``n``.
       
       EXAMPLES::
       
           sage: CGF_to_cyclotomic_form(5*(1-q^5)^-2*q^4)
           (5*q^4) * (q - 1)^-2 * (q^4 + q^3 + q^2 + q + 1)^-2
           
           sage: CGF_to_cyclotomic_form(5*(1-q^5)^-2*q^4, indexes_only=True)
           5*q^4 * 1^-2 * 5^-2
           
           sage: CGF_to_cyclotomic_form(5*(2-q^5)^-2*q^4)
           Traceback (most recent call last):
           ...
           ValueError: The polynomial 5*q^4/(q^10 - 4*q^5 + 4) is not cyclotomic due to the factor q^5 - 2'''
    f_fact = f.factor()
    cyc_fact = []
    unit = f_fact.unit()
    for g,mult in f_fact:
        if g == q:
            unit *= q^mult
            continue
        for n in euler_phi_inverse(g.degree()):
            c = cached_cyclotomic_polynomial(n)
            if g == c:
                if indexes_only:
                    c = n
                cyc_fact.append( (c, mult) )
                break
        else:
            # g is not a cyclotomic polynomial
            raise ValueError("The polynomial %s is not cyclotomic due to the factor %s"%(str(f), str(g)))
    return Factorization(cyc_fact, unit=unit)

def CGF_to_rational_form(f, indexes_only=False):
    '''Takes a polynomial `f(q)`. Returns a factorization of `f` consisting of a
       constant times `q`-integers (possibly to negative powers) and `q`'s. Raises an error if
       `f` cannot be so factored.
       
       Note: the powers of ``q`` are collected onto the unit portion of the
       factorization. Also allows powers of ``q-1`` as part of the unit.
       
       INPUT:
       
       - ``f`` - a polynomial in one variable `q`
       - ``indexes_only`` - boolean (default: ``False``). If ``True``, replaces the
         `q`-integer ``[n]_q`` with simply ``n``.
       
       EXAMPLES::
       
           sage: CGF_to_rational_form(5*(1-q^5)^-2*q^4*(1-q^6)^2)
           (5*q^4) * (q^2 - q + 1)^2 * (q^4 + q^3 + q^2 + q + 1)^-2
           
           sage: CGF_to_rational_form(5*(1-q^5)^-2*q^4*(1-q^6)^2, indexes_only=True)
           5*q^4 * 5^-2 * 6^2
           
           sage: f = 5*(1-q^5)^-2*q^4
           sage: CGF_to_rational_form(f).value() == f
           True
           
           sage: f = sum(q^T.standard_major_index() for T in StandardTableaux([3, 3]))
           sage: CGF_to_rational_form(f, indexes_only=True) # Contrast with q-hook length formula
           q^3 * 2^-1 * 3^-1 * 5 * 6'''
    cyc_form = CGF_to_cyclotomic_form(f, indexes_only=True)
    unit = cyc_form.unit()
    cyc_fact = dict(cyc_form)
    ret = []
    while len(cyc_fact) > 0:
        m = max(cyc_fact)
        if m==1:
            unit *= (q-1)^cyc_fact[1]
            break
        e = cyc_fact[m]
        if indexes_only:
            ret.append( (m, e) )
        else:
            ret.append( (cached_cyclotomic_polynomial(m), e) )
        for d in divisors(m):
            if d != 1:
                if d in cyc_fact:
                    cyc_fact[d] -= e
                else:
                    cyc_fact[d] = -e
        cyc_fact = {k:v for k,v in cyc_fact.items() if v != 0}
    return Factorization(ret, unit=unit)

def CGF_to_rational_AB(f):
    '''Takes a polynomial `f(q)`. Returns a pair of lists A, B where
       `f` is ``\\prod_{a \\in A} [a]_q/\\prod_{b \\in B} [b]_q'', up to
       a `q`-shift, unit, and factors of ``q-1``. The lists A, B
       are the same length and have trivial intersection, which ensures
       they are unique.
    
       INPUT:
       
       - ``f`` - a polynomial in one variable `q`
       
       EXAMPLES::
       
           sage: CGF_to_rational_AB(5*(1-q^5)^-2*q^4*(1-q^6)^2*(1-q^7)/(1-q))
           ([7, 6, 6], [5, 5, 1])
           
           sage: f = sum(q^T.standard_major_index() for T in StandardTableaux([3, 3]))
           sage: CGF_to_rational_AB(f) # Contrast with q-hook length formula
           ([6, 5], [3, 2])'''
    f_fact = CGF_to_rational_form(f, indexes_only=True)
    A = []
    B = []
    for g,mult in f_fact:
        if mult > 0:
            for _ in range(mult):
                A.append(g)
        else:
            for _ in range(-mult):
                B.append(g)
    if len(A) > len(B):
        for _ in range(len(A)-len(B)):
            B.append(1)
    else:
        for _ in range(len(B)-len(A)):
            A.append(1)
    return sorted(A,reverse=True),sorted(B,reverse=True)

def is_CGF(f, check_nonnegative=True):
    '''Takes a polynomial `f(q)` over QQ and determines if it is a
       product of cyclotomic polynomials, up to an overall constant and
       `q` shift.
       
       Note: does not ensure the coefficients of `f` are nonnegative integers.
       
       INPUT:
       
       - ``f`` - a polynomial in one variable `q`
       - ``check_nonnegative`` - boolean (default: ``True``). If ``True``, ensures
         the coefficients are nonnegative.
       
       EXAMPLES::
       
           sage: is_CGF(5*(1-q^5)^-2*q^4*(1-q^6)^2*(1-q^7)/(1-q))
           True
           
           sage: is_CGF(1+3*q+q^2)
           False
           
           sage: is_CGF(1-2*q+q^2)
           False
           
           sage: is_CGF(1-2*q+q^2, check_nonnegative=False)
           True'''
    try:
        CGF_to_cyclotomic_form(f, indexes_only=True)
        if check_nonnegative:
            return _is_nonnegative(list(f))
        else:
            return True
    except:
        return False

#------------------------------------------------------
#------------------- Phi_PM routines ------------------
#------------------------------------------------------

def Phi_PM(n, indexes_only=False):
    '''Takes an integer `n` and iterates over ``\\Phi^{\\pm}_n``, i.e.
       all products of cyclotomic polynomials of total degree `n`.
       
       INPUT:
       
       - ``n`` - a positive integer
       - ``indexes_only`` - boolean (default: ``False``). If ``True``, replaces the
         ``Phi_m(q)`` with simply ``m`` and returns a sorted list of such ``m``.
       
       EXAMPLES::
       
           sage: list(Phi_PM(2))
           [q^2 + q + 1, q^2 + 1, q^2 - q + 1, q^2 - 2*q + 1, q^2 - 1, q^2 + 2*q + 1]
           
           sage: list(Phi_PM(2, indexes_only=True))
           [[3], [4], [6], [1, 1], [1, 2], [2, 2]]
           
           sage: oeis([sum(1 for _ in Phi_PM(n)) for n in range(1,12)])
           0: A120963: Number of monic polynomials with integer coefficients of degree n with all roots on the unit circle; number of products of cyclotomic polynomials of degree n.
           '''
    factors = tuple(euler_phi_inverse(deg) for deg in range(n+1))
    # factors[i] is the list of all m such that euler_phi(m) = i+1
    if indexes_only:
        for la in Partitions(n):
            for LL in itertools.product(*(comps(factors[deg+1], mult) for deg, mult in enumerate(la.to_exp()) if mult > 0)):
                yield sorted(flatten(LL))
    else:
        for la in Partitions(n):
            for LL in itertools.product(*(comps(factors[deg+1], mult) for deg, mult in enumerate(la.to_exp()) if mult > 0)):
                yield _cyclotomic_form_to_polynomial(flatten(LL))

def Phi_PM_irreds(n):
    '''Takes an integer `n` and returns a list of all irreducible elements of
       ``\\Phi^{\\pm}_n``, i.e. all cyclotomic polynomials of degree `n`.
       
       INPUT:
       
       - ``n`` - a positive integer
       
       EXAMPLES::
       
           sage: Phi_PM_irreds(4)
           [q^4 + q^3 + q^2 + q + 1, q^4 + 1, q^4 - q^3 + q^2 - q + 1, q^4 - q^2 + 1]
           
           sage: oeis([len(Phi_PM_irreds(n)) for n in range(1,12)])
           0: A014197: Number of numbers m with Euler phi(m) = n.'''
    return list(map(cached_cyclotomic_polynomial, euler_phi_inverse(n)))

#------------------------------------------------------
#------------------- Phi_P routines -------------------
#------------------------------------------------------

def _is_nonnegative(L):
    return all(_ >= 0 for _ in L)

def Phi_P(n, indexes_only=False):
    '''Takes an integer `n` and iterates over ``\\Phi^{+}_n``, i.e.
       all products of cyclotomic polynomials of total degree `n` with
       non-negative coefficients.
       
       INPUT:
       
       - ``n`` - a positive integer
       - ``indexes_only`` - boolean (default: ``False``). If ``True``, replaces the
         ``Phi_m(q)`` with simply ``m`` and returns a sorted list of such ``m``.
       
       EXAMPLES::
       
           sage: list(Phi_P(3))
           [q^3 + 2*q^2 + 2*q + 1, q^3 + q^2 + q + 1, q^3 + 1, q^3 + 3*q^2 + 3*q + 1]
           
           sage: list(Phi_P(3, indexes_only=True))
           [[2, 3], [2, 4], [2, 6], [2, 2, 2]]
           
           sage: oeis([sum(1 for _ in Phi_P(n)) for n in range(1,12)])
           0: A360620: Number of basic cyclotomic generating functions of degree n.'''
    if indexes_only:
        for L in Phi_PM(n, indexes_only=True):
            if _is_nonnegative(list(_cyclotomic_form_to_polynomial(L))):
                yield L
    else:
        for f in Phi_PM(n):
            if _is_nonnegative(list(f)):
                yield f

@cached_function
def Phi_P_irreds(n):
    '''Takes an integer `n` and returns a list of all irreducible elements of
       ``\\Phi^{+}_n``, i.e. all products of cyclotomic polynomials of
       total degree `n` with non-negative coefficients.
       
       INPUT:
       
       - ``n`` - a positive integer
       
       EXAMPLES::
       
           sage: Phi_P_irreds(2)
           [q^2 + q + 1, q^2 + 1]
           
           sage: oeis([len(Phi_P_irreds(n)) for n in range(1,12)])
           0: A361441: The number of generators for the monoid of basic cyclotomic generating functions of degree n.'''
    if n == 0:
        return []

    ret = []
    irreds = [Phi_P_irreds(i) for i in range(n)]
    
    def _is_irred(f):
        for i in range(1,n):
            for g in irreds[i]:
                q, r = f.quo_rem(g)
                if r != 0:
                    continue
                if _is_nonnegative(list(q)):
                    return False
        return True

    for f in Phi_P(n):
        # Check if L is a product of lower irreducibles
        if _is_irred(f):
            ret.append(f)
    return ret

#------------------------------------------------------
#------------------ Phi_Gale routines -----------------
#------------------------------------------------------

def _is_Gale(f):
    A,B = CGF_to_rational_AB(f)
    return all(A[i] >= B[i] for i in range(len(A)))

def Phi_Gale(n, indexes_only=False):
    '''Takes an integer `n` and iterates over ``\\Phi^{Gale}_n``, i.e.
       all products of cyclotomic polynomials of total degree `n` with
       non-negative coefficients and where rational AB form has A >= B in sorted
       componentwise order.
       
       INPUT:
       
       - ``n`` - a positive integer
       - ``indexes_only`` - boolean (default: ``False``). If ``True``, replaces the
         ``Phi_m(q)`` with simply ``m`` and returns a sorted list of such ``m``.
       
       EXAMPLES::
       
           sage: list(Phi_Gale(3))
           [q^3 + 2*q^2 + 2*q + 1, q^3 + q^2 + q + 1, q^3 + 1, q^3 + 3*q^2 + 3*q + 1]
           
           sage: list(Phi_Gale(3, indexes_only=True))
           [[2, 3], [2, 4], [2, 6], [2, 2, 2]]
           
           sage: [sum(1 for _ in Phi_Gale(n)) for n in range(1,12)]
           [1, 3, 4, 10, 12, 27, 33, 68, 82, 154, 187]'''
    if indexes_only:
        for L in Phi_PM(n, indexes_only=True):
            f = _cyclotomic_form_to_polynomial(L)
            coeffs = list(f)
            if _is_nonnegative(coeffs) and _is_Gale(f):
                yield L
    else:
        for f in Phi_PM(n):
            coeffs = list(f)
            if _is_nonnegative(coeffs) and _is_Gale(f):
                yield f

@cached_function
def Phi_Gale_irreds(n):
    '''Takes an integer `n` and returns a list of all irreducible elements of
       ``\\Phi^{Gale}_n``, i.e. all products of cyclotomic polynomials of total
       degree `n` with non-negative coefficients and where rational AB form has
       A >= B in sorted componentwise order.
       
       INPUT:
       
       - ``n`` - a positive integer
       
       EXAMPLES::
       
           sage: Phi_Gale_irreds(2)
           [q^2 + q + 1]
           
           sage: [len(Phi_Gale_irreds(n)) for n in range(1,12)]
           [1, 2, 1, 3, 1, 4, 1, 6, 1, 5, 1]'''
    if n == 0:
        return []

    ret = []
    irreds = [Phi_Gale_irreds(i) for i in range(n)]
    
    def _is_irred(f):
        for i in range(1,n):
            for g in irreds[i]:
                q, r = f.quo_rem(g)
                if r != 0:
                    continue
                coeffs = list(q)
                if _is_nonnegative(coeffs) and _is_Gale(q):
                    return False
        return True

    for f in Phi_Gale(n):
        # Check if L is a product of lower irreducibles
        if _is_irred(f):
            ret.append(f)
    return ret

#------------------------------------------------------
#------------------ Phi_uni routines ------------------
#------------------------------------------------------

def _is_unimodal(L):
    i = 1
    end = len(L)
    while i < end and L[i - 1] <= L[i]:
        i += 1
    while i < end and L[i - 1] >= L[i]:
        i += 1
    return i == end

def Phi_uni(n, indexes_only=False):
    '''Takes an integer `n` and iterates over ``\\Phi^{uni}_n``, i.e.
       all products of cyclotomic polynomials of total degree `n` with
       non-negative, unimodal coefficients.
       
       INPUT:
       
       - ``n`` - a positive integer
       - ``indexes_only`` - boolean (default: ``False``). If ``True``, replaces the
         ``Phi_m(q)`` with simply ``m`` and returns a sorted list of such ``m``.
       
       EXAMPLES::
       
           sage: list(Phi_uni(3))
           [q^3 + 2*q^2 + 2*q + 1, q^3 + q^2 + q + 1, q^3 + 3*q^2 + 3*q + 1]
           
           sage: list(Phi_uni(3, indexes_only=True))
           [[2, 3], [2, 4], [2, 2, 2]]
           
           sage: oeis([sum(1 for _ in Phi_uni(n)) for n in range(1,12)])
           0: A360621: Number of basic unimodal cyclotomic generating functions of degree n.'''
    if indexes_only:
        for L in Phi_PM(n, indexes_only=True):
            coeffs = list(_cyclotomic_form_to_polynomial(L))
            if _is_nonnegative(coeffs) and _is_unimodal(coeffs):
                yield L
    else:
        for f in Phi_PM(n):
            coeffs = list(f)
            if _is_nonnegative(coeffs) and _is_unimodal(coeffs):
                yield f

@cached_function
def Phi_uni_irreds(n):
    '''Takes an integer `n` and returns a list of all irreducible elements of
       ``\\Phi^{uni}_n``, i.e. all products of cyclotomic polynomials of
       total degree `n` with non-negative, unimodal coefficients.
       
       INPUT:
       
       - ``n`` - a positive integer
       
       EXAMPLES::
       
           sage: Phi_uni_irreds(2)
           [q^2 + q + 1]
           
           sage: oeis([len(Phi_uni_irreds(n)) for n in range(1,12)])
           0: A361440: The number of generators for the monoid of basic unimodal cyclotomic generating functions of degree n.'''
    if n == 0:
        return []

    ret = []
    irreds = [Phi_uni_irreds(i) for i in range(n)]
    
    def _is_irred(f):
        for i in range(1,n):
            for g in irreds[i]:
                q, r = f.quo_rem(g)
                if r != 0:
                    continue
                coeffs = list(q)
                if _is_nonnegative(coeffs) and _is_unimodal(coeffs):
                    return False
        return True

    for f in Phi_uni(n):
        # Check if L is a product of lower irreducibles
        if _is_irred(f):
            ret.append(f)
    return ret

#------------------------------------------------------
#------------------ Phi_lcc routines ------------------
#------------------------------------------------------

def _is_lcc(L):
    '''Assumes the input does not have leading or trailing 0's and is non-negative.'''
    if any(i <= 0 for i in L):
        return False
    return all(L[i]^2 >= L[i-1] * L[i+1] for i in range(1, len(L)-1))


def Phi_lcc(n, indexes_only=False):
    '''Takes an integer `n` and iterates over ``\\Phi^{lcc}_n``, i.e.
       all products of cyclotomic polynomials of total degree `n` with
       non-negative, log-concave coefficients with no internal zeros.
       
       INPUT:
       
       - ``n`` - a positive integer
       - ``indexes_only`` - boolean (default: ``False``). If ``True``, replaces the
         ``Phi_m(q)`` with simply ``m`` and returns a sorted list of such ``m``.
       
       EXAMPLES::
       
           sage: list(Phi_lcc(3))
           [q^3 + 2*q^2 + 2*q + 1, q^3 + q^2 + q + 1, q^3 + 3*q^2 + 3*q + 1]
           
           sage: list(Phi_uni(3, indexes_only=True))
           [[2, 3], [2, 4], [2, 2, 2]]
           
           sage: oeis([sum(1 for _ in Phi_lcc(n)) for n in range(1,12)])
           0: A360622: Number of basic log-concave (with no internal zeros) cyclotomic generating functions of degree n.'''
    if indexes_only:
        for L in Phi_PM(n, indexes_only=True):
            coeffs = list(_cyclotomic_form_to_polynomial(L))
            if _is_nonnegative(coeffs) and _is_lcc(coeffs):
                yield L
    else:
        for f in Phi_PM(n):
            coeffs = list(f)
            if _is_nonnegative(coeffs) and _is_lcc(coeffs):
                yield f

@cached_function
def Phi_lcc_irreds(n):
    '''Takes an integer `n` and returns a list of all irreducible elements of
       ``\\Phi^{lcc}_n``, i.e. all products of cyclotomic polynomials of
       total degree `n` with non-negative, log-concave coefficients with
       no internal zeros.
       
       INPUT:
       
       - ``n`` - a positive integer
       
       EXAMPLES::
       
           sage: Phi_lcc_irreds(2)
           [q^2 + q + 1]
           
           sage: oeis([len(Phi_lcc_irreds(n)) for n in range(1,12)])
           0: A361440: The number of generators for the monoid of basic unimodal cyclotomic generating functions of degree n.'''
    if n == 0:
        return []

    ret = []
    irreds = [Phi_lcc_irreds(i) for i in range(n)]
    
    def _is_irred(f):
        for i in range(1,n):
            for g in irreds[i]:
                q, r = f.quo_rem(g)
                if r != 0:
                    continue
                coeffs = list(q)
                if _is_nonnegative(coeffs) and _is_lcc(coeffs):
                    return False
        return True

    for f in Phi_lcc(n):
        # Check if L is a product of lower irreducibles
        if _is_irred(f):
            ret.append(f)
    return ret


## Examples ##

### 1. CGF testing and conversions ###

#### a. Test if $f(q)$ is a CGF ####

In [2]:
# The major index generating functions for standard tableaux of fixed partition shape are CGF's
la = Partition([4, 2, 2])
f_maj = sum(q^T.standard_major_index() for T in StandardTableaux(la)); f_maj

q^20 + q^19 + 3*q^18 + 3*q^17 + 5*q^16 + 5*q^15 + 7*q^14 + 6*q^13 + 7*q^12 + 5*q^11 + 5*q^10 + 3*q^9 + 3*q^8 + q^7 + q^6

In [3]:
# Verify f_maj is a CGF
is_CGF(f_maj)

True

In [4]:
# By contrast, 1+q+q^3 is not cyclotomic
is_CGF(1+q+q^3)

False

#### b. Convert a CGF to cyclotomic form ####

In [5]:
# Write f_maj as a product of cyclotomic polynomials, with a q-shift
CGF_to_cyclotomic_form(f_maj)

(q^6) * (q^2 + 1)^2 * (q^4 + 1) * (q^6 + q^5 + q^4 + q^3 + q^2 + q + 1)

In [6]:
# Give only the indexes of the cyclotomic polynomials
CGF_to_cyclotomic_form(f_maj, indexes_only=True)

q^6 * 4^2 * 7 * 8

#### c. Convert a CGF to rational form ####

In [7]:
# Write f_maj as a ratio of products of q-integers
CGF_to_rational_form(f_maj)

(q^6) * (q + 1)^-2 * (q^2 + 1) * (q^4 + 1) * (q^6 + q^5 + q^4 + q^3 + q^2 + q + 1)

In [8]:
# Give only the indexes of the q-integers
CGF_to_rational_form(f_maj, indexes_only=True)

q^6 * 2^-2 * 4 * 7 * 8

In [9]:
# Give only the multisets of q-integers in the numerator and denominator
CGF_to_rational_AB(f_maj)

([8, 7, 4], [2, 2, 1])

In [10]:
# Those multisets agree with the multisets from the q-hook formula up to cancellation
(list(range(sum(la),1,-1)), la.hooks())

([8, 7, 6, 5, 4, 3, 2], [6, 5, 3, 2, 2, 2, 1, 1])

#### d. Operations with Factorizations ####

In [11]:
# Ensure the value of the Factorization is correct
CGF_to_cyclotomic_form(f_maj).value() == f_maj

True

In [12]:
# Pick off the q-shift/constant portion
CGF_to_cyclotomic_form(f_maj).unit()

q^6

In [13]:
# List the cyclotomic factors with their multiplicities
list(CGF_to_cyclotomic_form(f_maj, indexes_only=True))

[(4, 2), (7, 1), (8, 1)]

### 2. Cyclotomic monoids ###

#### a. Iterating over monoids and irreducibles by degree ####

In [14]:
# Iterate over the positive cyclotomic monoid in degree 4
list(Phi_P(4))

[q^4 + q^3 + q^2 + q + 1,
 q^4 + 1,
 q^4 + 2*q^3 + 3*q^2 + 2*q + 1,
 q^4 + q^3 + 2*q^2 + q + 1,
 q^4 + q^2 + 1,
 q^4 + 2*q^2 + 1,
 q^4 + 3*q^3 + 4*q^2 + 3*q + 1,
 q^4 + 2*q^3 + 2*q^2 + 2*q + 1,
 q^4 + q^3 + q + 1,
 q^4 + 4*q^3 + 6*q^2 + 4*q + 1]

In [15]:
# Iterate over the unimodal cyclotomic monoid in degree 4,
#   showing only cyclotomic indexes
list(Phi_uni(4, indexes_only=True))

[[5], [3, 3], [3, 4], [2, 2, 3], [2, 2, 4], [2, 2, 2, 2]]

#### b. Appendix tables ####

In [16]:
# Compute the number of elements in various cyclotomic monoids
#   for degrees 1 through 11
print([sum(1 for _ in Phi_lcc(n)) for n in range(1,12)])
print([sum(1 for _ in Phi_uni(n)) for n in range(1,12)])
print([sum(1 for _ in Phi_Gale(n)) for n in range(1,12)])
print([sum(1 for _ in Phi_P(n)) for n in range(1,12)])
print([sum(1 for _ in Phi_PM(n)) for n in range(1,12)])

[1, 2, 3, 5, 7, 12, 16, 26, 35, 53, 70]
[1, 2, 3, 6, 8, 14, 20, 34, 48, 72, 100]
[1, 3, 4, 10, 12, 27, 33, 68, 82, 154, 187]
[1, 3, 4, 10, 12, 27, 33, 68, 82, 154, 189]
[2, 6, 10, 24, 38, 78, 118, 224, 330, 584, 838]


In [17]:
# Compute the number of irreducible elements
#   for degrees 1 through 11
print([len(Phi_lcc_irreds(n)) for n in range(1,12)])
print([len(Phi_uni_irreds(n)) for n in range(1,12)])
print([len(Phi_Gale_irreds(n)) for n in range(1,12)])
print([len(Phi_P_irreds(n)) for n in range(1,12)])
print([len(Phi_PM_irreds(n)) for n in range(1,12)])

[1, 1, 1, 1, 1, 2, 2, 4, 4, 7, 8]
[1, 1, 1, 2, 2, 3, 4, 7, 10, 9, 15]
[1, 2, 1, 3, 1, 4, 1, 6, 1, 5, 1]
[1, 2, 1, 3, 1, 4, 1, 6, 1, 5, 3]
[2, 3, 0, 4, 0, 4, 0, 5, 0, 2, 0]
